In [3]:
import pandas as pd

In [72]:
from current import grid, count_moves, determine_directions
class Locator:
    """ This object returns dataframes containing the information about other ships/shipyards on the map and also in the given ship's grid. """
    def __init__(self, board, ship):
        self.board = board
        self.ship = ship
        self.ship_position = ship.position
        # Get the grid
        self.grid = grid(ship.cell)

    def get_ship_info(self):
        """ Returns the info about ships in all of the board. """
        ships_info = {}

        for ship_id, ship in self.board.ships.items():
            base_info = {"my_ship": 0, "moves": 0, "position": (ship.position.x, ship.position.y),
                         'cargo': ship.cell.halite, 'moves': count_moves(self.ship.position, ship.position),
                         'dirX': (determine_directions(self.ship_position, ship.position))[0],
                         'dirY': (determine_directions(self.ship_position, ship.position))[1]}

            base_info['movesX'] = min(abs(self.ship_position.x - ship.position.x), abs(21 - self.ship_position.x + ship.position.x))
            base_info['movesY'] = min(abs(self.ship_position.y - ship.position.y), abs(21 - self.ship_position.y + ship.position.y))

            if ship_id in self.board.current_player.ship_ids and ship.id != self.ship.id:
                base_info['my_ship'] = 1
                ships_info[ship_id] = base_info
            elif not (ship_id in self.board.current_player.ship_ids):
                ships_info[ship_id] = base_info

        return pd.DataFrame(ships_info)

    def get_shipyard_info(self):
        """ Returns the info about shipyards in all of the board. """
        shipyards_info = {}

        for shipyard_id, shipyard in self.board.shipyards.items():
            base_info = {"my_shipyard": 0,
                         "position": (shipyard.position.x, shipyard.position.y),
                         'dirX': (determine_directions(self.ship_position, shipyard.position))[0],
                         'dirY': (determine_directions(self.ship_position, shipyard.position))[1],
                         'player_halite': shipyard.player.halite,
                         'moves': count_moves(self.ship.position, shipyard.position)}

            base_info['movesX'] = min(abs(self.ship_position.x - ship.position.x), abs(21 - self.ship_position.x + ship.position.x))
            base_info['movesY'] = min(abs(self.ship_position.y - ship.position.y), abs(21 - self.ship_position.y + ship.position.y))

            if shipyard_id in self.board.current_player.shipyard_ids:
                base_info['my_shipyard'] = 1
                shipyards_info[shipyard_id] = base_info
            else:
                shipyards_info[shipyard_id] = base_info

        return pd.DataFrame(shipyards_info)

    def generate_grid_df(self):
        """ Generates a Dataframe describing the information of objects and cells in the 5x5 grid of the ship. """
        all_dirs = {}

        total_moves = len(self.grid) / 4
        
        for direction, cell in self.grid.items():

            base_info = {
                "ship_id": None, "shipyard_id": None,
                "my_ship": 0, "my_shipyard": 0,
                "halite": 0, "moves": 0,
                "movesX": 0, "movesY": 0,
                "dirY": 'None', "dirX": 'None',
                'weightX': 0, 'weightY': 0
            }

            if "N" in  direction:
                base_info['dirY'] = 'N'
                base_info['movesY'] = direction.count("N")
            elif "S" in  direction:
                base_info['dirY'] = 'S'
                base_info['movesY'] = direction.count("S")

            if "W" in  direction:
                base_info['dirX'] = 'W'
                base_info['movesX'] = direction.count("W")
            elif "E" in  direction:
                base_info['dirX'] = 'E'
                base_info['movesX'] = direction.count("E")

            if base_info['dirY'] != 'None':
                base_info['weightY'] = (total_moves - base_info['movesY']) / (base_info['movesY'] * total_moves)
            
            if base_info['dirX'] != 'None':
                base_info['weightX'] = (total_moves - base_info['movesX']) / (base_info['movesX'] * total_moves)


            if cell.ship is not None:
                base_info["ship_id"] = cell.ship.id
                if cell.ship.id in self.ship.player.ship_ids:
                    base_info["my_ship"] = 1

            if cell.shipyard is not None:
                base_info["shipyard_id"] = cell.shipyard.id
                if cell.shipyard.id in self.ship.player.shipyard_ids:
                    base_info['my_shipyard'] = 1

            base_info['halite'] = cell.halite
            # The number of letters in the direction would indicate the number of moves needed to get there
            base_info['moves'] = len(direction)

            all_dirs[direction] = base_info

        return pd.DataFrame(all_dirs)

In [1]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

# Create a test environment for use later
board_size = 21
environment = make("halite", configuration={"size": board_size, "startingHalite": 30000}, debug=True)
agent_count = 4
environment.reset(agent_count)
state = environment.state[0]

In [73]:
# Change the behviour of my own movement from board.current_player
board = Board(state.observation, environment.configuration)

board.current_player.ships[0].next_action = ShipAction.CONVERT
board.ships['0-2'].next_action = ShipAction.CONVERT
board.ships['0-3'].next_action = ShipAction.CONVERT
board.ships['0-4'].next_action = ShipAction.CONVERT
board = board.next()
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
# Opponents
board.ships['2-2'].next_action = ShipAction.NORTH
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.ships['2-3'].next_action = ShipAction.WEST
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.ships['2-4'].next_action = ShipAction.EAST
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.NORTH
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.ships['2-3'].next_action = ShipAction.NORTH
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.ships['2-4'].next_action = ShipAction.SOUTH
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.NORTH
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

board.current_player.ships[0].next_action = ShipAction.CONVERT
board = board.next()

ship = board.current_player.ships[0]
loc = Locator(board, ship)

In [ ]:
class ShipyardDecisions:
    def __init__(self, board: Board, shipyards: [Shipyard]):
        """
            Decides the Shipyard's next action based on the given parameters
            board: The board that we will be observing
            shipyards: All the shipyards that the player has
        """
        self.board = board
        self.Shipyards = shipyards

    def determine(self):
        """ Determines which shipyards should SPAWN, returns a dictionary of id: 'SPAWN' """
        pass

    def weight_shipyard_tendencies(self):
        """ Iterates through the shipyards and weights their tendencies. """
        for shipyard in self.Shipyards:
            grid = Locator(self.board, shipyard).generate_grid_df()
            weight = self.weight(self, grid)

    def weight(self, grid):
        """
            The weighting system is rather simple:
                - If there was an enemy ship add to the weight
                - If there was one of my own ships, then subtract from the weight
            Take the distance of the ship into acount
        """
        pass
            


In [81]:
loc.generate_grid_df().iloc[:,20:35]

21.0


SEE       NEE       SWW       NWW      NNNN      SSSS  \
ship_id          None      None      None      None      None      None   
shipyard_id      None      None      None      None      None      None   
my_ship             0         0         0         0         0         0   
my_shipyard         0         0         0         0         0         0   
halite         50.193    50.193    10.757    10.757         0         0   
moves               3         3         3         3         4         4   
movesX              2         2         2         2         0         0   
movesY              1         1         1         1         4         4   
dirY                S         N         S         N         N         S   
dirX                E         E         W         W      None      None   
weightX      0.452381  0.452381  0.452381  0.452381         0         0   
weightY      0.952381  0.952381  0.952381  0.952381  0.202381  0.202381   

                 WWWW      EEEE      EESS      EENN      WWNN      WWSS  \
ship_id          None      None      None      None      None      None   
shipyard_id      None      None      None      None      None      None   
my_ship             0         0         0         0         0         0   
my_shipyard         0         0         0         0         0         0   
halite         25.097       500         0         0         0         0   
moves               4         4         4         4         4         4   
movesX              4         4         2         2         2         2   
movesY              0         0         2         2         2         2   
dirY             None      None         S         N         N         S   
dirX                W         E         E         E         W         W   
weightX      0.202381  0.202381  0.452381  0.452381  0.452381  0.452381   
weightY             0         0  0.452381  0.452381  0.452381  0.452381   

                 WWWS      EEES      EEEN  
ship_id          None      None      None  
shipyard_id      None      None      None  
my_ship             0         0         0  
my_shipyard         0         0         0  
halite        136.241         0         0  
moves               4         4         4  
movesX              3         3         3  
movesY              1         1         1  
dirY                S         S         N  
dirX                W         E         E  
weightX      0.285714  0.285714  0.285714  
weightY      0.952381  0.952381  0.952381

In [71]:
ship.position

(5, 10)

In [86]:
loc.get_ship_info()

4-1       2-2     2-3      2-4
my_ship         1         0       0        0
moves           9        13       7       21
position  (9, 15)  (11, 17)  (8, 6)  (16, 0)
cargo           0         0       0  169.142
dirX            E         E       E        W
dirY            N         N       S        S
movesX          4         6       3       11
movesY          5         7       4       10

In [39]:
l = {"A": 2}
len(l)

1

In [111]:
%%writefile current.py

Overwriting current.py


In [5]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

env = make("halite", debug=True)
env.run(["random", "current.py", 'random', 'agent_a.py'])
env.render(mode="ipython", width=800, height=600)